In [1]:
def print_section(text):
    print('##############################################')
    print('###  ', text)
    print('##############################################')


print_section('Start imports')

import os
import sys
import pathlib
sys.path.append(str(pathlib.PurePath(pathlib.Path.cwd().parent)))

import tqdm
import numpy as np
import pickle
import marshal
import pandas as pd
import matplotlib.cm as cm
import matplotlib.axes as am
import matplotlib.pyplot as plt
%matplotlib widget

import dimod
import dwave
import dwave.system
from dwave.system import DWaveSampler, EmbeddingComposite, FixedEmbeddingComposite
import dwave.inspector
import dwave_networkx as dnx
import minorminer

from src.particle_funcs import distance_matrix as distance_matrix
from src.particle_funcs import io as particles_io
import src.leap_funcs.qubo.q_matrix as q_matrix

from src import leap_funcs as leap_funcs
from src.leap_funcs import embedding_quality
from src.leap_funcs.qubo import parameterstudy

from src import h5py_funcs
from src.h5py_funcs import inspections, discoveries, init_custom_getstates, io, parameterstudy_using_info_file

print_section('Finished imports')


##############################################
###   Start imports
##############################################
no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
##############################################
###   Finished imports
##############################################


In [2]:
import io
print('io.DEFAULT_BUFFER_SIZE', io.DEFAULT_BUFFER_SIZE)

io.DEFAULT_BUFFER_SIZE 8192


In [3]:
dict_files_information = {
    'study_mainname': 'sub',
    'info_file_mainname': 'study_params',
    'samples_folder_name': 'samples',
    'embeddings_folder_name': 'embeddings',
    'embeddings_file_mainname': 'emb_5_5_mm01.h5',
    'dict_studies_substudies' : {
        1: [''],
        2: [''],
        3: ['', "_2"],
        4: ['', "_2"],
        5: ['', "_1_1", "_2", "_3", "_3_2"],
        6: ['_1', "_1_2", "_2", "_2_2"],
        7: ['_1', "_1_2", "_1_3", "_1_4", "_1_5"],
        8: ['_1']
    },
    'dict_infofilenames': {
        1: ['study_nearest_neighbours_info.h5'],
        2: ['study_params_small.h5'],
        3: ['study_params_sub3.h5', 'study_params_sub3_2.h5'],
        4: ['study_params_sub4.h5', 'study_params_sub4_2.h5'],
        5: ['study_params_sub5.h5', 'study_params_sub5_1_1.h5', 'study_params_sub5_2.h5', 'study_params_sub5_3.h5', 'study_params_sub5_3_2.h5'],
        6: ['study_params_sub6_1.h5', 'study_params_sub6_1_2.h5', 'study_params_sub6_2.h5', 'study_params_sub6_2_2.h5'],
        7: ['study_params_sub7_1.h5', 'study_params_sub7_1_2.h5', 'study_params_sub7_1_3.h5', 'study_params_sub7_1_4.h5', 'study_params_sub7_1_5.h5'],
        8: ['study_params_sub8_1.h5']
    },
    'dict_study_dirnames': {
        1: ['sub_1'],
        2: ['sub_2'],
        3: ['sub_3', 'sub_3_2'],
        4: ['sub_4', 'sub_4_2'],
        5: ['sub_5', 'sub_5_1_1', 'sub_5_2', 'sub_5_3', 'sub_5_3_2'],
        6: ['sub_6_1', 'sub_6_1_2', 'sub_6_2', 'sub_6_2_2'],
        7: ['sub_7_1', 'sub_7_1_2', 'sub_7_1_3', 'sub_7_1_4', 'sub_7_1_5'],
        8: ['sub_8_1'] 
    },
    'dict_study_dir_name_paths': {...},
    'dict_info_file_name_paths': {...},
    

}
dict_files_information['dict_study_dir_name_paths'] = {i: [pathlib.Path.cwd().joinpath('01_out', f[j]) for j in range(len(f))] for i,f in dict_files_information['dict_study_dirnames'].items()}
dict_files_information['dict_info_file_name_paths'] = {i: [pathlib.Path.joinpath(dirs[j], dict_files_information['dict_infofilenames'][i][j]) for j in range(len(dirs))] for i,dirs in dict_files_information['dict_study_dir_name_paths'].items()}
assert np.all([f[j].exists() for i,f in dict_files_information['dict_info_file_name_paths'].items() for j in range(len(f))]), "Some info files do not exist"
dict_files_information

{'study_mainname': 'sub',
 'info_file_mainname': 'study_params',
 'samples_folder_name': 'samples',
 'embeddings_folder_name': 'embeddings',
 'embeddings_file_mainname': 'emb_5_5_mm01.h5',
 'dict_studies_substudies': {1: [''],
  2: [''],
  3: ['', '_2'],
  4: ['', '_2'],
  5: ['', '_1_1', '_2', '_3', '_3_2'],
  6: ['_1', '_1_2', '_2', '_2_2'],
  7: ['_1', '_1_2', '_1_3', '_1_4', '_1_5'],
  8: ['_1']},
 'dict_infofilenames': {1: ['study_nearest_neighbours_info.h5'],
  2: ['study_params_small.h5'],
  3: ['study_params_sub3.h5', 'study_params_sub3_2.h5'],
  4: ['study_params_sub4.h5', 'study_params_sub4_2.h5'],
  5: ['study_params_sub5.h5',
   'study_params_sub5_1_1.h5',
   'study_params_sub5_2.h5',
   'study_params_sub5_3.h5',
   'study_params_sub5_3_2.h5'],
  6: ['study_params_sub6_1.h5',
   'study_params_sub6_1_2.h5',
   'study_params_sub6_2.h5',
   'study_params_sub6_2_2.h5'],
  7: ['study_params_sub7_1.h5',
   'study_params_sub7_1_2.h5',
   'study_params_sub7_1_3.h5',
   'study_param

In [4]:
print_section('Read info files - Start')
dict_infos_read = {i: [h5py_funcs.inspections.read_info_file_to_dict(info_file_name_path=ifp[j], infoset_name = 'info') for j in range(len(ifp))]  
                   for i,ifp in dict_files_information['dict_info_file_name_paths'].items()}
#print(dict_infos_read)
print_section('Read info files - Finished')

##########
#
# The following test fails, because comparing dicts throws an error (below) when arrays are encountered, thats why it is left to the user to make sure the subs are compatible with the main study.
# "The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()" 
#
#########
#if len(info_file_name_path)>1:
#    for i in range(len(info_file_name_path)):
#        for key, value in dict_infos_read[0].items():
#            if key=='time_history': continue
#            else:
#                print(key)
#                if isinstance(value, np.ndarray):
#                    assert (value == dict_infos_read[i][key]).all(), print(value, dict_infos_read[i][key])
#                else:
#                    try: value == dict_infos_read[i][key]
#                    except Exception as e:
#                        print(e)
#                        print(value)
#                        print(dict_infos_read[i][key])

##############################################
###   Read info files - Start
##############################################
##############################################
###   Read info files - Finished
##############################################


In [5]:
list(dict_infos_read.keys())
list(dict_infos_read[1][0].keys())

['attrs',
 'DEMs',
 'nearest_neighbours',
 'qubos',
 'embs_files',
 'study',
 'time_history']

In [6]:
print(list(dict_infos_read.keys()))
print(list(len(dict_infos_read[i]) for i in dict_infos_read.keys()))
print(list(list(len(dict_infos_read[i][j]) for j in range(len(dict_infos_read[i]))) for i in dict_infos_read.keys()))
print(list(list(list(len(dict_infos_read[i][j][list(dict_infos_read[i][j].keys())[k]]) for k in range(len(dict_infos_read[i][j]))) for j in range(len(dict_infos_read[i]))) for i in dict_infos_read.keys()))

[1, 2, 3, 4, 5, 6, 7, 8]
[1, 1, 2, 2, 5, 4, 5, 1]
[[7], [7], [7, 7], [7, 7], [7, 7, 7, 7, 7], [7, 7, 7, 7], [7, 7, 7, 7, 7], [7]]
[[[2, 2, 5, 29, 2, 2, 30]], [[4, 2, 1, 1, 2, 2, 2049]], [[4, 2, 1, 1, 2, 2, 513], [4, 2, 1, 1, 2, 2, 513]], [[4, 2, 1, 1, 2, 2, 513], [4, 2, 1, 1, 2, 2, 513]], [[4, 2, 1, 1, 2, 2, 1001], [4, 2, 1, 1, 2, 2, 1001], [4, 2, 1, 1, 2, 2, 4097], [4, 2, 1, 1, 2, 2, 4097], [4, 2, 1, 1, 2, 2, 4097]], [[4, 2, 1, 1, 2, 2, 2601], [4, 2, 1, 1, 2, 2, 2601], [4, 2, 1, 1, 2, 2, 2601], [4, 2, 1, 1, 2, 2, 2601]], [[4, 2, 1, 1, 2, 2, 2817], [4, 2, 1, 1, 2, 2, 2817], [4, 2, 1, 1, 2, 2, 2817], [4, 2, 1, 1, 2, 2, 2817], [4, 2, 1, 1, 2, 2, 2817]], [[4, 2, 1, 1, 2, 2, 353]]]


In [7]:
print_section('Check read info files for unfinished runs - Start')
#print(dict_infos_read[0]['time_history'])
for i in dict_infos_read.keys():
    for j in range(len(dict_infos_read[i])):
        _tmp = []
        for key, value in dict_infos_read[i][j]['time_history'].items():
            if key == 'attrs':
                continue
            else:
                if not value['attrs']['finished']:
                    _tmp.append(key)
        print('unfinished param sets:', 'study', i, j, len(_tmp), _tmp)
print('done with separate dicts, now go with merged dict')
_tmp = []
for key, value in dict_infos_read[1][0]['time_history'].items():
    if key == 'attrs':
        continue
    else:
        if not value['attrs']['finished']:
            _tmp.append(key)
print('unfinished param sets:', len(_tmp), _tmp)
del _tmp
print_section('Check read info files for unfinished runs - Finished')

##############################################
###   Check read info files for unfinished runs - Start
##############################################
unfinished param sets: study 1 0 0 []
unfinished param sets: study 2 0 1584 ['zz_2126781597', 'zz_7117431879', 'zz_3832120126', 'zz_9814586425', 'zz_2766388070', 'zz_3534968685', 'zz_5852011708', 'zz_6545690208', 'zz_3051503396', 'zz_2838550192', 'zz_8457311102', 'zz_2352441897', 'zz_5082562948', 'zz_6696525060', 'zz_3816855651', 'zz_0775094796', 'zz_6648367505', 'zz_5242024204', 'zz_8288028865', 'zz_3647103428', 'zz_0923337296', 'zz_4700162007', 'zz_4918905980', 'zz_0741523063', 'zz_1393256340', 'zz_3962344985', 'zz_5738739335', 'zz_7224196042', 'zz_4022773375', 'zz_7617559026', 'zz_3853597685', 'zz_0283275865', 'zz_9903113606', 'zz_5764290520', 'zz_4422267000', 'zz_5521921709', 'zz_4737948565', 'zz_8268766743', 'zz_1679294747', 'zz_5376338274', 'zz_7704952570', 'zz_8497969207', 'zz_6692372646', 'zz_8609108227', 'zz_5361372428', 'zz_0576

In [8]:
#list_studies = list(dict_info_read['time_history'].keys())
#list_studies.remove('attrs')
#print('list of all studies:', len(list_studies), list_studies)

dict_studies = {key: [[v for v in val[j]['time_history'] if v != 'attrs'] for j in range(len(val))] for key, val in dict_infos_read.items()}
for key, val in dict_studies.items():
    print(key, len(val), [len(v) for v in val])

1 1 [29]
2 1 [2048]
3 2 [512, 512]
4 2 [512, 512]
5 5 [1000, 1000, 4096, 4096, 4096]
6 4 [2600, 2600, 2600, 2600]
7 5 [2816, 2816, 2816, 2816, 2816]
8 1 [352]


In [9]:
#print(dict_info_read['time_history']['zz_7293366434']['data'][2].decode('utf-8')[:4] == '2024')
#print(dict_info_read['time_history']['zz_7293366434']['attrs']['finished'])

In [10]:
print_section('Check read info files for unfinished runs again - Start')
for i, study in dict_studies.items():
    for j, submission in enumerate(study):
        for id in submission:
            # not marked as finished, but timestamp for finishing samples was updated from initial value (1910-...)
            if (not dict_infos_read[i][j]['time_history'][id]['attrs']['finished'])\
                and (dict_infos_read[i][j]['time_history'][id]['data'][2].decode('utf-8')[:4] in ('2024', '2025')):
                print('here 1', i, j, id)
            # marked as finished, but timestamp for finishing samples still has initial value (1910-...)
            elif dict_infos_read[i][j]['time_history'][id]['attrs']['finished']\
                and (dict_infos_read[i][j]['time_history'][id]['data'][2].decode('utf-8')[:4] not in ('2024', '2025')):
                print('here 1_2', i, j, id)
            # (optimal case) marked as finished, and timestamp for finishing samples was updated
            elif dict_infos_read[i][j]['time_history'][id]['attrs']['finished']\
                and (dict_infos_read[i][j]['time_history'][id]['data'][2].decode('utf-8')[:4] in ('2024', '2025')):
                #print('here 2')
                continue
            # not marked as finished, and timestamp for finishing samples was not updated
            elif (not dict_infos_read[i][j]['time_history'][id]['attrs']['finished'])\
                and (dict_infos_read[i][j]['time_history'][id]['data'][2].decode('utf-8')[:4] not in ('2024', '2025')):
                # timestamp for starting samples was not updated as well (everything ok, was just not started)
                if dict_infos_read[i][j]['time_history'][id]['data'][1].decode('utf-8')[:4] not in ('2024', '2025'):
                    pass
                # timestamp for starting samples was updated, but not for finishing samples, also the study was not marked as finished (unfortunate but ok, did just not complete)
                else:
                    print('here 1_3', i, j, id)
            else:
                print('here else', i, j, id, dict_infos_read[i][j]['time_history'][id]['attrs']['finished'], dict_infos_read[i][j]['time_history'][id]['data'][2].decode('utf-8'))
                # for key, value in dict_infos_read.items():
                #     if '2024' == value['time_history'][stud]['data'][2].decode('utf-8')[:4]:
                #         dict_info_read['time_history'][stud]['data'][1] = (value['time_history'][stud]['data'][1]+'.'.encode('utf-8'))[:-1]
                #         dict_info_read['time_history'][stud]['data'][2] = (value['time_history'][stud]['data'][2]+'.'.encode('utf-8'))[:-1]
                #         dict_info_read['time_history'][stud]['attrs']['finished'] = True
print('if this is the only line printed, then all studies in the info file are finished')
print_section('Check read info files for unfinished runs again - Finished')

##############################################
###   Check read info files for unfinished runs again - Start
##############################################
here 1_3 2 0 zz_2126781597
here 1_3 2 0 zz_7117431879
here 1_3 2 0 zz_3832120126
here 1_3 2 0 zz_9814586425
here 1_3 2 0 zz_2766388070
here 1_3 2 0 zz_3534968685
here 1_3 2 0 zz_5852011708
here 1_3 2 0 zz_6545690208
here 1_3 2 0 zz_3051503396
here 1_3 2 0 zz_2838550192
here 1_3 2 0 zz_8457311102
here 1_3 2 0 zz_2352441897
here 1_3 2 0 zz_5082562948
here 1_3 2 0 zz_6696525060
here 1_3 2 0 zz_3816855651
here 1_3 2 0 zz_0775094796
here 1_3 2 0 zz_6648367505
here 1_3 2 0 zz_5242024204
here 1_3 2 0 zz_8288028865
here 1_3 2 0 zz_3647103428
here 1_3 2 0 zz_0923337296
here 1_3 2 0 zz_4700162007
here 1_3 2 0 zz_4918905980
here 1_3 2 0 zz_0741523063
here 1_3 2 0 zz_1393256340
here 1_3 2 0 zz_3962344985
here 1_3 2 0 zz_5738739335
here 1_3 2 0 zz_7224196042
here 1_3 2 0 zz_4022773375
here 1_3 2 0 zz_7617559026
here 1_3 2 0 zz_3853597685
here 1_

In [11]:
print_section('Check estimated runtime - Start')
study_read = dict_infos_read[2][0]['study']['data'] 
study_read.dtype.names
est_runts = study_read['sets']['estimated_runtime'] * 10 # 10 runs per set #not available for dict_infos_read[1]
cum_est_runts = np.sum(est_runts)
#print(est_runts)
print('cummulative estimated runtime for 10000 samples each is [h]:', cum_est_runts/3600)
del study_read, est_runts, cum_est_runts
print_section('Check estimated runtime - Finished')


##############################################
###   Check estimated runtime - Start
##############################################
cummulative estimated runtime for 10000 samples each is [h]: 34.925406085774114
##############################################
###   Check estimated runtime - Finished
##############################################


In [12]:
print_section('Extract run identifiers and separate into un-/finished - Start')
array_identifiers, started_psets, finished_psets = {}, {}, {}
for i, study in dict_infos_read.items():
    array_identifiers[i], started_psets[i], finished_psets[i] = zip(*[h5py_funcs.inspections.extract_identifiers(dict_info_read = substudy) for substudy in study])

for i in dict_infos_read.keys():
    for j in range(len(dict_infos_read[i])):
        print('merged dict:', i, j)
        print('  started_psets:', started_psets[i][j])
        print('  finished_psets:', finished_psets[i][j])
        print('  {p1}/{p2} p_sets have been started, \n {p3}/{p2} p_sets have been finished'.format(p1=len(started_psets[i][j]), p2=array_identifiers[i][j].shape[0], p3=len(finished_psets[i][j])))

for i in dict_infos_read.keys():
    print('from individual runs accumulated:')
    print('  list_started_psets:', started_psets[i])
    print('  list_finished_psets:', finished_psets[i])
    print('  {p1}/{p2} p_sets have been started, \n {p3}/{p2} p_sets have been finished'.\
          format(p1=[len(l) for l in started_psets[i]], p2=[len(l) for l in array_identifiers[i]], p3=[len(l) for l in finished_psets[i]]))
print_section('Extract run identifiers and separate into un-/finished - Finished')

##############################################
###   Extract run identifiers and separate into un-/finished - Start
##############################################
merged dict: 1 0
  started_psets: [np.bytes_(b'zz_5703083384'), np.bytes_(b'zz_5457588972'), np.bytes_(b'zz_1897573298'), np.bytes_(b'zz_8272243285'), np.bytes_(b'zz_1070242504'), np.bytes_(b'zz_9469440848'), np.bytes_(b'zz_1692397523'), np.bytes_(b'zz_4165436873'), np.bytes_(b'zz_9880612622'), np.bytes_(b'zz_6856154368'), np.bytes_(b'zz_4931925256'), np.bytes_(b'zz_2057909975'), np.bytes_(b'zz_0054522459'), np.bytes_(b'zz_4885882981'), np.bytes_(b'zz_3979500108'), np.bytes_(b'zz_3088371157'), np.bytes_(b'zz_8129145255'), np.bytes_(b'zz_4435430247'), np.bytes_(b'zz_4179325359'), np.bytes_(b'zz_4076809715'), np.bytes_(b'zz_5334518067'), np.bytes_(b'zz_5412174942'), np.bytes_(b'zz_6018269281'), np.bytes_(b'zz_1561967451'), np.bytes_(b'zz_7127866328'), np.bytes_(b'zz_8171500250'), np.bytes_(b'zz_1908483939'), np.bytes_(b'zz_6057

In [ ]:
print_section('Define read from/write to params - Start')
list_possibilities_read_from = ['sample_data', 'pickle']
list_possibilities_write_to = ['pickle'] # 'marshal unmarshals numpy.ndarray as bytes-object and raises error when marshaling pathlib.Path objects'
read_from = 'sample_data'
write_to = 'pickle'
assert write_to == 'pickle', 'marshal unmarshals numpy.ndarray as bytes-object and raises error when marshaling pathlib.Path objects'
print('  read_from:', read_from, ' , possibilities:', list_possibilities_read_from)
print('  write_to:', write_to, ' , possibilities:', list_possibilities_write_to)
dict_for_df = {}
print_section('Define read from/write to params - Finished')

##############################################
###   Define read from/write to params - Start
##############################################
  read_from: sample_data  , possibilities: ['sample_data', 'pickle']
  write_to: marshal  , possibilities: ['pickle', 'marshal', 'None']
##############################################
###   Define read from/write to params - Finished
##############################################


In [14]:
if read_from == 'sample_data':
    print_section('Read from sample data - Start')
    assert len(dict_infos_read) == len(dict_files_information['dict_study_dirnames'])
    dict_for_df = {}
    for i in dict_infos_read.keys():
        print('reading from sample data for study', i)
        # dict_for_df[i] = {k:v for d in h5py_funcs.inspections.read_answers_to_dict_concurrent(samples_folder_name_path = 
        #                                                                         [dict_files_information['dict_study_dir_name_paths'][i][j].joinpath(
        #                                                                                                dict_files_information['samples_folder_name'])
        #                                                                                                for j in range(len(dict_files_information['dict_study_dir_name_paths'][i]))],
        #                                                                    array_identifiers = finished_psets[i],
        #                                                                     num_procs = 90, batch_size = 5)
        #                                 for k,v in d.items()}
        
        dict_for_df[i] = [{k: v for d in h5py_funcs.inspections.read_answers_to_dict_concurrent(samples_folder_name_path = 
                                                                                [dict_files_information['dict_study_dir_name_paths'][i][j].joinpath(
                                                                                                       dict_files_information['samples_folder_name'])],
                                                                           array_identifiers = [finished_psets[i][j]],
                                                                            num_procs = 90, batch_size = 5)
                                                                            for k,v in d.items()}
                                                                            for j in range(len(dict_files_information['dict_study_dir_name_paths'][i]))]
        
    print_section('Read from sample data - Finished')
    #_reads = h5py_funcs.inspections.read_answers_to_dict_concurrent(samples_folder_name_path,list_finished_psets, num_procs=75, batch_size=5)
    #for r in _reads:
    #    print(r.get())

##############################################
###   Read from sample data - Start
##############################################
reading from sample data for study 1
read_answers_to_dict_concurrent


[Parallel(n_jobs=90)]: Using backend LokyBackend with 90 concurrent workers.


no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
no cupy available, imported numpy as usual
no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
Custom getstate funct

[Parallel(n_jobs=90)]: Done   3 out of  29 | elapsed:    2.7s remaining:   23.0s
[Parallel(n_jobs=90)]: Done   6 out of  29 | elapsed:    2.9s remaining:   11.0s
[Parallel(n_jobs=90)]: Done   9 out of  29 | elapsed:    3.1s remaining:    6.9s
[Parallel(n_jobs=90)]: Done  12 out of  29 | elapsed:    3.2s remaining:    4.6s
[Parallel(n_jobs=90)]: Done  15 out of  29 | elapsed:    3.4s remaining:    3.2s
[Parallel(n_jobs=90)]: Done  18 out of  29 | elapsed:    3.6s remaining:    2.2s
[Parallel(n_jobs=90)]: Done  21 out of  29 | elapsed:    3.8s remaining:    1.4s
[Parallel(n_jobs=90)]: Done  24 out of  29 | elapsed:    4.1s remaining:    0.9s
[Parallel(n_jobs=90)]: Done  27 out of  29 | elapsed:    4.2s remaining:    0.3s
[Parallel(n_jobs=90)]: Done  29 out of  29 | elapsed:    4.4s finished
[Parallel(n_jobs=90)]: Using backend LokyBackend with 90 concurrent workers.


reading from sample data for study 2
read_answers_to_dict_concurrent
no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
no cupy available, imported numpy as usual
no cupy available, imported numpy as usual
no cupy available, imported numpy as usual
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding.FixedEmbeddingComposite have been initialized.
Custom getstate functions for dwave.cloud.config.models.ClientConfig, dwave.cloud.client.qpu.Client, dwave.cloud.solver.StructuredSolver, dwave.system.samplers.dwave_sampler.DWaveSampler, dwave.system.composites.embedding

...

[Parallel(n_jobs=90)]: Done 720 tasks      | elapsed:    0.2s
[Parallel(n_jobs=90)]: Done 845 tasks      | elapsed:    0.2s
[Parallel(n_jobs=90)]: Done 970 tasks      | elapsed:    0.3s
[Parallel(n_jobs=90)]: Done 1105 tasks      | elapsed:    0.3s
[Parallel(n_jobs=90)]: Done 1240 tasks      | elapsed:    0.3s
[Parallel(n_jobs=90)]: Done 1385 tasks      | elapsed:    0.3s
[Parallel(n_jobs=90)]: Done 1530 tasks      | elapsed:    0.4s
[Parallel(n_jobs=90)]: Done 1685 tasks      | elapsed:    0.4s
[Parallel(n_jobs=90)]: Done 1840 tasks      | elapsed:    0.4s
[Parallel(n_jobs=90)]: Done 2005 tasks      | elapsed:    0.5s
[Parallel(n_jobs=90)]: Done 2170 tasks      | elapsed:    0.5s
[Parallel(n_jobs=90)]: Done 2345 tasks      | elapsed:    0.5s
[Parallel(n_jobs=90)]: Done 2448 tasks      | elapsed:    0.5s
[Parallel(n_jobs=90)]: Done 2485 tasks      | elapsed:    0.6s
[Parallel(n_jobs=90)]: Done 2522 tasks      | elapsed:    0.6s
[Parallel(n_jobs=90)]: Done 2561 tasks      | elapsed:    

reading from sample data for study 8
read_answers_to_dict_concurrent


[Parallel(n_jobs=90)]: Done  16 tasks      | elapsed:    1.7s
[Parallel(n_jobs=90)]: Done  46 tasks      | elapsed:    3.0s
[Parallel(n_jobs=90)]: Done  76 tasks      | elapsed:    4.4s
[Parallel(n_jobs=90)]: Done 110 tasks      | elapsed:    6.1s
[Parallel(n_jobs=90)]: Done 143 tasks      | elapsed:    7.4s
[Parallel(n_jobs=90)]: Done 180 tasks      | elapsed:    9.1s
[Parallel(n_jobs=90)]: Done 200 tasks      | elapsed:    9.8s
[Parallel(n_jobs=90)]: Done 221 tasks      | elapsed:   10.5s
[Parallel(n_jobs=90)]: Done 242 tasks      | elapsed:   11.2s
[Parallel(n_jobs=90)]: Done 281 out of 352 | elapsed:   13.0s remaining:    3.3s
[Parallel(n_jobs=90)]: Done 317 out of 352 | elapsed:   14.7s remaining:    1.6s


##############################################
###   Read from sample data - Finished
##############################################


[Parallel(n_jobs=90)]: Done 352 out of 352 | elapsed:   16.1s finished


In [15]:
#dict_for_df[1]

In [16]:
#dict_for_df = {k: v for e in _reads for k,v in e.items()}

In [17]:
print(list(dict_for_df.keys()))
print(list(len(dict_for_df[i]) for i in dict_for_df.keys()))
print(len(list(e for e in list(dict_for_df[5][j] for j in range(len(dict_for_df[5]))))))
len(dict_for_df[5][0])
len(list(dict_for_df[5][0].keys()))


[1, 2, 3, 4, 5, 6, 7, 8]
[1, 1, 2, 2, 5, 4, 5, 1]
5


1000

In [18]:
######
#
# old version before concurrent read via joblib
#
######
#
#
#if read_from == 'sample_data':
#    print_section('Read from sample data - Start')
#
#    for sfnp, ids in zip(samples_folder_name_path,list_finished_psets):
#        # samples_folder_name_path is a list of all the submissions to be read
#        print('  reading from', sfnp)
#        _tmp_study_name = sfnp.parent.stem
#        print('  file name', _tmp_study_name)
#        dict_for_df |= h5py_funcs.inspections.read_answers_to_dict(\
#            samples_folder_name_path=sfnp\
#            , array_identifiers=np.array(ids))#[::25]
#    print(dict_for_df.__sizeof__()) # size in memory in bytes
#    print(len(dict_for_df)) # number of keys in dict
#    if write_to == 'pickle':
#        with open(pathlib.Path('01_out',f'dict_for_df_{_tmp_study_name}.txt'), 'wb') as f:
#            pickle.dump(dict_for_df, f, protocol=5)
#    del _tmp_study_name
#    print_section('Read from sample data - Finished')


In [19]:
######
#
# old version before concurrent read via joblib
#
######
#
#
# if read_from == 'pickle':
#    print_section('Read from pickle - Start')
#    with open(pathlib.Path('01_out',f'dict_for_df_{study_name}.txt'), 'rb') as f:
#        dict_for_df = pickle.load(f)
#    print_section('Read from pickle - Finished')

In [20]:
######
#
# old version before concurrent read via joblib
#
######
#
#
#is_combine_pickled_dicts = False
#if is_combine_pickled_dicts:
#    print_section('Combine dicts read via Pickle - Start')
#    in_dicts = ['01_out\\dict_for_df_sub_6_2.txt'\
#               ,'01_out\\dict_for_df_sub_6_2_2.txt']
#    out_dicts = ['01_out\\dict_for_df_sub_6_2_combined.txt']
#    out_dict = {}
#    for in_d in in_dicts:
#        print(f'  read {in_d}')
#        with open(in_d, 'rb') as f:
#            out_dict |= pickle.load(f)
#    print('  finished reading all in_dicts')
#    for key, val in out_dict.items():
#        sample_set_length = (len(val['custom']['sampleset'].keys()))
#        if sample_set_length != 10:
#            print(key, sample_set_length)
#    print_section('Combine dicts read via Pickle - Finished')

In [21]:
######
#
# old version before concurrent read via joblib
#
######
#
#
#if is_combine_pickled_dicts:
#    print_section('Write combined dicts read via Pickle to file - Start')
#    out_dicts = ['01_out\\dict_for_df_sub_5_3_combined.txt']
#    with open(out_dicts[0], 'wb') as f:
#        pickle.dump(out_dict, f, protocol=5)
#    print_section('Write combined dicts read via Pickle to file - Finished')

In [22]:
print_section('Obtain exact/correct solution via simulated annealing - Start')
import ast
import dwave.samplers

num_particles = 5
qubo = dict_infos_read[2][0]['qubos'][f'{num_particles}_{num_particles}']

#sim_annealing_sample = dimod.samplers.ExactSolver().sample_qubo(
#    {ast.literal_eval(key): value['data'] for key, value in qubo.items()})
sim_annealing_sample = dwave.samplers.SimulatedAnnealingSampler().sample_qubo(
    {ast.literal_eval(key): value['data'] for key, value in qubo.items()},
    num_reads=10000)
sim_annealing_sample = sim_annealing_sample.aggregate() # accumulates number of occurences
#print(type(sim_annealing_sample))
exact_sol = sim_annealing_sample.record
exact_sol.sort(order='energy')
#print(exact_sol)
print_section('Obtain correct solution via simulated annealing - Finished')

##############################################
###   Obtain exact/correct solution via simulated annealing - Start
##############################################
##############################################
###   Obtain correct solution via simulated annealing - Finished
##############################################


In [23]:
print_section('Extract success dict from info, samples, and correct solution - Start')
n_samples_to_compare = 3
n_exact_sols_to_compare = 3
#dir_name_path_plots = './01_out/'

dict_success = {}
for i in dict_for_df.keys():
    print('study', i, 'has', len(dict_for_df[i]), 'substudies', end=' ')
    # dict_success[i] = {key: h5py_funcs.inspections.extract_success_dict(\
    # dict_for_df = val\
    # , exact_sols = exact_sol\
    # , n_samples_to_compare = n_samples_to_compare\
    # , n_exact_sols_to_compare = n_exact_sols_to_compare) for key, val in dict_for_df[i].items()}

    dict_success[i] = [h5py_funcs.inspections.extract_success_dict(\
    dict_for_df = dict_for_df[i][j]\
    , exact_sols = exact_sol\
    , n_samples_to_compare = n_samples_to_compare\
    , n_exact_sols_to_compare = n_exact_sols_to_compare)
    for j in range(len(dict_for_df[i]))]

    print('and', len(dict_success[i]), 'were successful')
# success_dict = h5py_funcs.inspections.extract_success_dict(\
#     dict_for_df = dict_for_df\
#     , exact_sols = exact_sol\
#     , n_samples_to_compare = n_samples_to_compare\
#     , n_exact_sols_to_compare = n_exact_sols_to_compare)


#for key in success_dict.keys():
#    print(key, success_dict[key])
print_section('Extract success dict from info, samples, and correct solution - Finished')

##############################################
###   Extract success dict from info, samples, and correct solution - Start
##############################################
study 1 has 1 substudies and 1 were successful
study 2 has 1 substudies and 1 were successful
study 3 has 2 substudies and 2 were successful
study 4 has 2 substudies and 2 were successful
study 5 has 5 substudies and 5 were successful
study 6 has 4 substudies and 4 were successful
study 7 has 5 substudies and 5 were successful
study 8 has 1 substudies and 1 were successful
##############################################
###   Extract success dict from info, samples, and correct solution - Finished
##############################################


In [24]:
print_section('Extract started parameter sets from success dict - Start')
started_sets, study_matched_started_ids = {}, {}
for i in dict_for_df.keys():
    started_sets[i], study_matched_started_ids[i] = zip(*[h5py_funcs.inspections.extract_started_sets_from_success_dict(\
        success_dict = dict_success[i][j]\
        , dict_info_read = dict_infos_read[i][j]) for j in range(len(dict_infos_read[i]))])
#print(started_sets)
#print(study_matched_started_ids)
#print(study_matched_started_ids.dtype)
print_section('Extract started parameter sets from success dict - Finished')

##############################################
###   Extract started parameter sets from success dict - Start
##############################################
started_sets
 [b'zz_5703083384', b'zz_5457588972', b'zz_1897573298', b'zz_8272243285', b'zz_1070242504', b'zz_9469440848', b'zz_1692397523', b'zz_4165436873', b'zz_9880612622', b'zz_6856154368', b'zz_4931925256', b'zz_2057909975', b'zz_0054522459', b'zz_4885882981', b'zz_3979500108', b'zz_3088371157', b'zz_8129145255', b'zz_4435430247', b'zz_4179325359', b'zz_4076809715', b'zz_5334518067', b'zz_5412174942', b'zz_6018269281', b'zz_1561967451', b'zz_7127866328', b'zz_8171500250', b'zz_1908483939', b'zz_6057258587', b'zz_5706799265']
dict_info_read[study][data][identifiers]
 [b'zz_5703083384' b'zz_5457588972' b'zz_1897573298' b'zz_8272243285'
 b'zz_1070242504' b'zz_9469440848' b'zz_1692397523' b'zz_4165436873'
 b'zz_9880612622' b'zz_6856154368' b'zz_4931925256' b'zz_2057909975'
 b'zz_0054522459' b'zz_4885882981' b'zz_3979500108' b'zz_

In [ ]:
assert write_to == 'pickle', 'marshal unmarshals numpy.ndarray as bytes-object and raises error when marshaling pathlib.Path objects'
with open(pathlib.Path('03_inspect/01_data').joinpath('dict_files_information.' + 'pickle'), mode='wb') as f:
    # always requires pickle because of pathlib.Path is not marshallable
    pickle.dump(dict_files_information, f, protocol=5)
    

with open(pathlib.Path('03_inspect/01_data').joinpath('dict_infos_read.' + write_to), mode='wb') as f:
    if write_to == 'pickle':
        pickle.dump(dict_infos_read, f, protocol=5)
    elif write_to == 'marshal':
        marshal.dump(dict_infos_read, f)

for i in dict_for_df.keys():
    print('writing dicts for study', i, 'of', len(dict_for_df))
    dict_studies_mainname = 'dict_study_'
    dict_success_mainname = 'dict_success_'
    with open(pathlib.Path('03_inspect/01_data').joinpath(dict_studies_mainname + str(i) + '.' + write_to), mode='wb') as f:
        if write_to == 'pickle':
            pickle.dump(dict_for_df[i], f, protocol=5)
        elif write_to == 'marshal':
            marshal.dump(dict_for_df[i], f)
    with open(pathlib.Path('03_inspect/01_data').joinpath(dict_success_mainname + str(i) + '.' + write_to), mode='wb') as f:
        if write_to == 'pickle':
            pickle.dump(dict_success[i], f, protocol=5)
        elif write_to == 'marshal':
            marshal.dump(dict_success[i], f)

writing dicts for study 1 of 8
writing dicts for study 2 of 8
writing dicts for study 3 of 8
writing dicts for study 4 of 8
writing dicts for study 5 of 8
writing dicts for study 6 of 8
writing dicts for study 7 of 8
writing dicts for study 8 of 8


In [ ]:
dict_files_information